In [1]:
# If the libraries are not yet installed, they can be installed in this notebook using commands similar to the below
# %conda install numpy
# %conda install pandas
# %conda install scikit-learn
# %conda install -c conda-forge prophet

# Something like the following may also work if the above does not
# import sys
# !conda install --yes --prefix {sys.prefix} numpy
# !conda install --yes --prefix {sys.prefix} pandas
# !conda install --yes --prefix {sys.prefix} scikit-learn
# !conda install -c conda-forge --yes --prefix {sys.prefix} prophet

# To install a specific version, add the version to the install command
# E.g., %conda install numpy=1.20.3

# If all else fails, use pip or follow additional advice such as found at
# https://jakevdp.github.io/blog/2017/12/05/installing-python-packages-from-jupyter/

# If your plan to use pip (especially if you are not working within a specified conda environment), 
# the pip commands might look like:
# pip install numpy
# pip install pandas
# pip install scikit-learn
# pip install prophet

# To install a specific version, add the version to the pip install command
# E.g., pip install numpy==1.20.3

In [2]:
# Load necessary packages
import time
import pandas as pd
from prophet import Prophet
from prophet.diagnostics import cross_validation
from prophet.diagnostics import performance_metrics
import itertools
import numpy as np
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
import glob
import random
import os

Importing plotly failed. Interactive plots will not work.


In [3]:
# Create results directory
os.makedirs("Results/Univariate/Prophet/", exist_ok=True)

In [4]:
np.random.seed(54321)
random.seed(54321)

# Read in Data and Prepare for Modeling 

In [5]:
# Read in all csv files for England from the Processed directory and save in a list

# Create an empty list
england_df_list = list()

# Loop through all file names in alphebtical order to match R list.files function, 
# read into a pandas df, ensure each df is in chronological order, and append to list
for fname in sorted(glob.glob("Data/Processed/Highways_England/*.csv")):
    print("Reading {}".format(fname))
    df = pd.read_csv(fname)
    df = df.sort_values(by="timestamp")
    england_df_list.append(df)

Reading Data/Processed/Highways_England/A11-6310-1_Southbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A11-6312-2_Northbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A14-1107A_Eastbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A14-1144B_Westbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A1M-9842B_Southbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A1M-9847a_Northbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A46-7636-1_Northbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A46-7636-2_Southbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A47-6337-1_Westbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A47-6337-2_Eastbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A5-6847-2_Southbound_2019_Processed.csv
Reading Data/Processed/Highways_England/A5-7572-1-Northbound_2019_Processed.csv
Reading Data/Processed/Highways_Englan

In [6]:
# Read in all csv files for Portland form the Processed directory and save in a list
portland_df_list = list()

for fname in sorted(glob.glob("Data/Processed/Portland/*.csv")):
    print("Reading {}".format(fname))
    df = pd.read_csv(fname)
    df = df.sort_values(by="timestamp")
    portland_df_list.append(df)

Reading Data/Processed/Portland/I205-101068_Northbound_2019_Processed.csv
Reading Data/Processed/Portland/I205-101073_Southbound_2019_Processed.csv
Reading Data/Processed/Portland/I405-100395_Southbound_2019_Processed.csv
Reading Data/Processed/Portland/I405-100527_Northbound_2019_Processed.csv
Reading Data/Processed/Portland/I5-100688_Southbound_2019_Processed.csv
Reading Data/Processed/Portland/I5-100703_Northbound_2019_Processed.csv
Reading Data/Processed/Portland/I84-101108_Eastbound_2019_Processed.csv
Reading Data/Processed/Portland/I84-101161_Westbound_2019_Processed.csv
Reading Data/Processed/Portland/OR217-100300_Southbound_2019_Processed.csv
Reading Data/Processed/Portland/OR217-100314_Northbound_2019_Processed.csv
Reading Data/Processed/Portland/R2 Delta Hwy-101745_Northbound_2019_Processed.csv
Reading Data/Processed/Portland/R2 OR18-102111_Westbound_2019_Processed.csv
Reading Data/Processed/Portland/R2 OR18-102113_Eastbound_2019_Processed.csv
Reading Data/Processed/Portland/

In [7]:
# Read in all csv files for Utah from the Processed directory and save in a list
utah_df_list = list()

for fname in sorted(glob.glob("Data/Processed/Utah/*.csv")):
    print("Reading {}".format(fname))
    df = pd.read_csv(fname)
    df = df.sort_values(by="timestamp")
    utah_df_list.append(df)

Reading Data/Processed/Utah/I15-3103178_Southbound_2019_Processed.csv
Reading Data/Processed/Utah/I15-749_Northbound_2019_Processed.csv
Reading Data/Processed/Utah/I215-134_Counterclockwise_2019_Processed.csv
Reading Data/Processed/Utah/I215-31_Clockwise_2019_Processed.csv
Reading Data/Processed/Utah/I70-3103400_Westbound_2019_Processed.csv
Reading Data/Processed/Utah/I70-3103401_Eastbound_2019_Processed.csv
Reading Data/Processed/Utah/I80-600_Eastbound_2019_Processed.csv
Reading Data/Processed/Utah/I80-667_Westbound_2019_Processed.csv
Reading Data/Processed/Utah/I84-451_Eastbound_2019_Processed.csv
Reading Data/Processed/Utah/I84-482_Westbound_2019_Processed.csv
Reading Data/Processed/Utah/LegacyParkway-810_Northbound_2019_Processed.csv
Reading Data/Processed/Utah/LegacyParkway-890_Southbound_2019_Processed.csv
Reading Data/Processed/Utah/US189-260_Westbound_2019_Processed.csv
Reading Data/Processed/Utah/US189-470_Eastbound_2019_Processed.csv
Reading Data/Processed/Utah/US40-634_Westb

In [8]:
# Append all lists together to create one total list of data frames
total_df_list = england_df_list + portland_df_list + utah_df_list

In [9]:
# Read in the start and end points csv, and subtract 1 to deal with index differences between R and python
start_end = pd.read_csv("start_end_points.csv")
start_end["start"] = start_end["start"] - 1
start_end["end"] = start_end["end"]

In [10]:
# Sanity check
start_end.head()

start    end
0  11579  19643
1  17982  26046
2  14189  22253
3  24009  32073
4   3238  11302

In [11]:
# Initialize an empty list
subset_df_list = list()

# For each df in the total_df_list
for idx, df in enumerate(total_df_list):
    
    # subset the df using the start and end points
    subset_df = df.iloc[start_end.iloc[idx,0]:start_end.iloc[idx,1], ]\
    .reset_index(drop=True).reset_index(drop=False)\
    .rename(columns={"index":"rn"}) # Create a row_num col based on the index of the data frame
    
    # Create a train_val_test field to denote which set each observation is a part of
    subset_df["train_val_test"] = np.where(subset_df["rn"]<(96*7*8),
                                           "train",
                                           np.where(subset_df["rn"]<(96*7*10),
                                                    "val",
                                                    "test"
                                                   )
                                       )

    # Append the subset df to the list
    subset_df_list.append(subset_df)

In [12]:
# Create two lists, one for the train_val data and one for the test data
train_df_list = list()
test_df_list = list()

# Loop through the list of subset dfs
for df in subset_df_list:
    
    # Filter to train and val only for the training data
    train_df = df.query("train_val_test != 'test'").copy()
    train_df = train_df[['timestamp', 'total_volume']]\
    .rename(columns={'timestamp':'ds', 'total_volume':'y'}) # For prophet, we must rename our timestamp column to ds and out target to y
    
    # Append to list
    train_df_list.append(train_df)
    
    # Same steps for test df list
    test_df = df.query("train_val_test == 'test'").copy()
    test_df = test_df[['timestamp', 'total_volume']]\
    .rename(columns={'timestamp':'ds', 'total_volume':'y'})
    test_df_list.append(test_df)

# Fit Prophet Models via Cross Validation

In [13]:
# Set up a grid of params (in a dictionary) to use for cross validation
param_grid = {  
    'changepoint_prior_scale': [0.001, 0.01, 0.1, 0.5],
    'seasonality_prior_scale': [0.01, 0.1, 1.0, 10.0],
}

In [14]:
# Create a list of dictionaries of all param combos of interest
all_params = [dict(zip(param_grid.keys(), v)) \
              for v in itertools.product(*param_grid.values())]

## England

In [15]:
# Create an empty list to save best params for england
best_params = list()

In [16]:
# Initialize a start time to subtract from the end time to compute the run time of the loop for optimization
england_start_time = time.time()

# Loop through each training data frame
for idx, train_df in enumerate(train_df_list[0:len(england_df_list)]):
    print(idx)
    # Initialize an empty list to store RMSE
    rmses = [] 
    # Loop through the param combo we are going to test
    for params in all_params:
        # Instantiate and fit a model to the training data
        m = Prophet(**params).fit(train_df)
        # Run cross validation using a training period of 56 days, a forecast horizon of 7 days, and a step after
        # each evaluation of 3.5 days
        df_cv = cross_validation(m,  
                                 initial = '56 day', 
                                 period = '3.5 day', 
                                 horizon = '7 day',
                                 parallel = "processes")
        # Compute cross validation performance metrics
        df_p = performance_metrics(df_cv, rolling_window=1)
        # Append the RMSE from cross validation to the RMSE list
        rmses.append(df_p['rmse'].values[0])
        
    # Find the location of the min RMSE
    best_param = all_params[np.argmin(rmses)]
    # Append the params corresponding to the best RMSE to the best_params list
    best_params.append(best_param)
    
# Grab the current time after optimization to compute run time
england_end_time = time.time()


0


INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-06-30 02:44:00 and 2019-07-03 14:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36d4211910>


Initial log joint probability = -149.145
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12117.7   4.35026e-07       5144.16      0.2917           1      126   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     121       12117.7    3.3905e-09       4837.93       0.319       0.319      155   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance
Initial log joint probability = -201.797
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
Initial log joint probability = -157.33
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       9674.72   1.49417e-05       5162.96       0.271       0.271      121   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      62       10211.3   0.000438734       5060.57  

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-06-30 02:44:00 and 2019-07-03 14:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36d421df40>


Initial log joint probability = -149.145
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12408.8   6.24172e-06        4568.2           1           1      123   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       12412.5   1.14188e-08       5018.86      0.2292      0.2292      246   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     204       12412.5   7.23851e-09       5065.21      0.7869      0.7869      252   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance
Initial log joint probability = -201.797
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
Initial log joint probability = -157.33
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      92       10016.7   0.000590475       4548.29  

...

Initial log joint probability = -549.031
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       11944.7   0.000612467       48.9347           1           1      126   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199         11945   0.000942358       14.2526           1           1      246   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       11945.1   5.40593e-05       7.94504       0.942       0.942      361   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     399       11945.1   4.02579e-05       8.10158      0.3125           1      489   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     426       11945.1   1.18577e-05       12.3651   1.186e-06       0.001      565  LS failed, Hessian reset 
     452       11945.1   5.41187e-06    

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-11-14 14:14:00 and 2019-11-18 02:14:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36d421df40>


Initial log joint probability = -549.031
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       11949.6    0.00174466       70.4555           1           1      121   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       11949.9   0.000108223       12.6134       1.256      0.1256      238   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299         11950     0.0001639       16.8244     0.06176           1      357   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     399       11950.1   0.000783503       45.0754           1           1      472   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     436       11950.1   1.31869e-05       6.58424   4.844e-07       0.001      560  LS failed, Hessian reset 
Optimization terminated normally: 
  Con

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-11-14 14:14:00 and 2019-11-18 02:14:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36f4957250>


Initial log joint probability = -549.031
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       11949.7   0.000797434        41.083           1           1      119   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199         11950   5.40462e-05       19.6175      0.5534      0.5534      237   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       11950.1    0.00219619       25.2861           1           1      360   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     391       11950.1    9.2703e-06       7.84436    5.57e-07       0.001      516  LS failed, Hessian reset 
     399       11950.1    1.0821e-05       7.20196     0.08452      0.2392      527   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     499       11950.1   0.000345236    

In [18]:
round(england_end_time - england_start_time, 2)

3136.15

In [19]:
# Save performance to a data frame and write to a csv file
england_best_params = pd.DataFrame(best_params)
england_best_params.to_csv("Results/Univariate/Prophet/england_best_params_prophet.csv", index=False)

## Portland

In [20]:
# Follow the exact same procedure for Portland and Utah data

In [21]:
best_params = list()

In [22]:
portland_start_time = time.time()
for idx, train_df in enumerate(train_df_list[len(england_df_list):(len(england_df_list)+len(portland_df_list))]):
    print(idx)
    rmses = [] 
    for params in all_params:
        m = Prophet(**params).fit(train_df)
        df_cv = cross_validation(m,  
                                 initial = '56 day', 
                                 period = '3.5 day', 
                                 horizon = '7 day',
                                 parallel = "processes")
        df_p = performance_metrics(df_cv, rolling_window=1)
        rmses.append(df_p['rmse'].values[0])
        
    best_param = all_params[np.argmin(rmses)]
    best_params.append(best_param)
portland_end_time = time.time()

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


0


INFO:prophet:Making 2 forecasts with cutoffs between 2019-05-08 06:44:00 and 2019-05-11 18:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36a02205b0>


Initial log joint probability = -148.112
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      94       14926.6   5.17811e-09       4497.82       0.131       0.131      132   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance
Initial log joint probability = -92.7513
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
Initial log joint probability = -162.186
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      79       12571.6   0.000170285       4169.02   4.186e-08       0.001      133  LS failed, Hessian reset 
      99       13357.4   1.92427e-05       3290.21      0.1828      0.8327      131   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12572.7   1.35657e-06       3808.55      0.4789      0.4789      158   
    Iter      log prob        ||

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-05-08 06:44:00 and 2019-05-11 18:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f369b56efa0>


...

Initial log joint probability = -521.291
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       10185.6     0.0218665       980.304      0.4205           1      121   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       10212.9     0.0132514       248.854      0.3146           1      235   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       10221.3     0.0171647       60.7606           1           1      345   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     399       10225.1    0.00399648       54.6871      0.2543           1      459   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     499       10227.4    0.00139807       13.7404           1           1      577   
    Iter      log prob        ||dx||      ||grad||       alpha  

    1499       9189.84   0.000899279       23.7517           1           1     1961   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1599       9190.02    0.00101219       27.5751     0.08596           1     2080   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1604       9190.03   1.92969e-05       9.54223   1.108e-06       0.001     2126  LS failed, Hessian reset 
    1686       9190.22    1.5783e-05       8.44252   2.262e-06       0.001     2281  LS failed, Hessian reset 
    1699       9190.22   1.82945e-05       21.0655      0.1626      0.1626     2297   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1736       9190.23   1.44554e-05       6.84261    1.06e-06       0.001     2384  LS failed, Hessian reset 
    1764       9190.24   2.86649e-06       5.71616      0.3014           1     2422   
Optimization terminated normally: 
  Conver

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-08-09 01:44:00 and 2019-08-12 13:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36a01e6190>


Initial log joint probability = -521.291
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       10187.4     0.0150913       582.112      0.4911     0.04911      123   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       10209.7    0.00206929       80.9968           1           1      234   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       10217.3     0.0254616       500.381      0.1978      0.1978      342   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     399       10224.3      0.135995       530.854           1           1      450   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     499       10227.5    0.00487091        36.233       1.346      0.1346      563   
    Iter      log prob        ||dx||      ||grad||       alpha  

    1199       9189.55     0.0107963       49.9245           1           1     1463   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1295       9189.76   2.62311e-05       13.7139   1.846e-06       0.001     1620  LS failed, Hessian reset 
    1299       9189.76   0.000263343       8.80512       4.552           1     1628   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1305       9189.76   7.03342e-06       4.10819      0.1523           1     1636   
Optimization terminated normally: 
  Convergence detected: relative gradient magnitude is below tolerance


In [23]:
round(portland_end_time - portland_start_time, 2)

1993.32

In [24]:
portland_best_params = pd.DataFrame(best_params)

In [25]:
portland_best_params.to_csv("Results/Univariate/Prophet/portland_best_params_prophet.csv", index=False)

## Utah

In [26]:
best_params = list()

In [27]:
utah_start_time = time.time()
for idx, train_df in enumerate(train_df_list[(len(england_df_list)+len(portland_df_list)):len(train_df_list)]):
    print(idx)
    rmses = [] 
    for params in all_params:
        m = Prophet(**params).fit(train_df)
        df_cv = cross_validation(m,  
                                 initial = '56 day', 
                                 period = '3.5 day', 
                                 horizon = '7 day',
                                 parallel = "processes")
        df_p = performance_metrics(df_cv, rolling_window=1)
        rmses.append(df_p['rmse'].values[0])
        
    best_param = all_params[np.argmin(rmses)]
    best_params.append(best_param)
utah_end_time = time.time()

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


0


INFO:prophet:Making 2 forecasts with cutoffs between 2019-05-30 12:44:00 and 2019-06-03 00:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36a00bdc40>


Initial log joint probability = -381.351
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       14362.4   1.13967e-05       4930.21      0.7341      0.7341      129   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     108       14363.8   0.000253031          5297   5.601e-08       0.001      188  LS failed, Hessian reset 
     199       14365.1   4.25789e-08       4795.88           1           1      302   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     203       14365.1   8.17254e-09       4559.56      0.3206      0.3206      307   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance
Initial log joint probability = -174.726
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
Initial log joint probability = -333.786
    Iter      log prob        ||

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-05-30 12:44:00 and 2019-06-03 00:44:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f369b569490>


...

Initial log joint probability = -258.426
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12969.8    0.00259474       90.4269      0.6395      0.6395      128   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       12975.7    0.00404995       678.782      0.2434           1      245   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       12977.6    0.00136755       74.6869           1           1      356   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     399       12978.6   0.000980315       76.8157      0.2529           1      475   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     499       12979.2     0.0114245       40.6342           1           1      591   
    Iter      log prob        ||dx||      ||grad||       alpha  

    1299       11098.3   0.000158633       17.3013           1           1     1617   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1199       11670.9   0.000150081       31.1344     0.05409      0.2342     1507   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1238       11670.9    1.1366e-05       14.1374   7.601e-07       0.001     1594  LS failed, Hessian reset 
    1345       11098.3   1.70245e-05       15.6853   1.581e-06       0.001     1716  LS failed, Hessian reset 
    1353       11098.3     9.339e-06       7.79847           1           1     1726   
Optimization terminated normally: 
  Convergence detected: relative gradient magnitude is below tolerance
    1299       11670.9   0.000194793        16.953           1           1     1668   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1399       11671.2    0.00102944       37.17

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:prophet:Making 2 forecasts with cutoffs between 2019-07-04 16:59:00 and 2019-07-08 04:59:00
INFO:prophet:Applying in parallel with <concurrent.futures.process.ProcessPoolExecutor object at 0x7f36a24efb50>


Initial log joint probability = -258.426
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12970.8     0.0262545       601.193           1           1      133   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       12976.5    0.00976177        91.041           1           1      247   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       12977.5     0.0015825       65.8237           1           1      361   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     399       12978.5    0.00103521       30.9895           1           1      466   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     499       12979.6      0.023338       60.5947           1           1      585   
    Iter      log prob        ||dx||      ||grad||       alpha  

    1787       11671.6   1.77526e-05       21.6508   7.435e-07       0.001     2221  LS failed, Hessian reset 
    1799       11671.6   0.000128432       9.75144      0.8533      0.8533     2234   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1899       11671.7    0.00046369       20.4096       0.438       0.438     2353   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    1999       11671.7   0.000231247       8.58428           1           1     2469   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    2099       11671.8    0.00283784       45.9947           1           1     2586   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
    2199       11671.9   5.06233e-05       19.1156      0.1698      0.1698     2708   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  N

In [28]:
round(utah_end_time - utah_start_time, 2)

1844.43

In [29]:
utah_best_params = pd.DataFrame(best_params)

In [30]:
utah_best_params.to_csv("Results/Univariate/Prophet/utah_best_params_prophet.csv", index=False)

# Forecast with Prophet Models Found Above

In [31]:
# Read in the params from the previously created CSV files
england_params = pd.read_csv("Results/Univariate/Prophet/england_best_params_prophet.csv")
portland_params = pd.read_csv("Results/Univariate/Prophet/portland_best_params_prophet.csv")
utah_params = pd.read_csv("Results/Univariate/Prophet/utah_best_params_prophet.csv")

# Append all dfs into 1
total_params = england_params.append(portland_params).append(utah_params)

In [32]:
# Create empty lists to store performance metrics
# Because one-step ahead forecasts do not work the same as with models like ARIMA, we compute
# 1-day ahead, 1-week ahead, and 2-week ahead predictions for the prophet models
rmse_1_day_list = list()
mae_1_day_list = list()
rmse_1_week_list = list()
rmse_2_week_list = list()
mae_1_week_list = list()
mae_2_week_list = list()

# Create empty dictionaries to save some forecast data (a new model must be created for each PI level)
# Also, initialize counters to store run time information
forecast_dict = dict()
forec_time_tot = 0
forecast_dict_95 = dict()
forec_time_95_tot = 0

mod_list = list()
mod_fit_time_tot = 0
mod_95_list = list()
mod_fit_time_95_tot = 0

forec_start_time = time.time()
for i in range(len(train_df_list)):
    # Get the model params for each respective time series
    model_params = total_params.iloc[i,].to_dict()
    # Create a copy dictionary of the params so that a second model with a 95% PI can be created
    model_params_95 = model_params.copy()
    
    # Add the interval widths to the sets of model params
    model_params['interval_width']=0.8
    model_params_95['interval_width']=0.95
    
    # Create the models for each PI level and make the forecasts
    # Get the start time for model fitting
    mod_fit_start = time.time()
    # Create the model
    mod = Prophet(**model_params)
    # Fit the model
    mod.fit(train_df_list[i])
    # Get the end time for model fitting and add the total fitting time to the counter
    mod_fit_end = time.time()
    mod_fit_time = mod_fit_end - mod_fit_start
    mod_fit_time_tot += mod_fit_time
    mod_list.append(mod)
    
    # Get the start time for computing forecasts
    forec_start_time = time.time()
    # Compute forecasts
    forecasts = mod.predict(test_df_list[i])
    # Get the end time, compute the total time spent forecasting, and add to the counter
    forec_end_time = time.time()
    forec_time = forec_end_time - forec_start_time
    forec_time_tot += forec_time
    
    # Do the same steps for the models for 95% PI as were done above for the 80% PI models
    mod_fit_95_start = time.time()
    mod_95 = Prophet(**model_params_95)
    mod_95.fit(train_df_list[i])
    mod_fit_95_end = time.time()
    mod_fit_time_95 = mod_fit_95_end - mod_fit_95_start
    mod_fit_time_95_tot += mod_fit_time_95
    mod_95_list.append(mod_95_list)
    
    forec_start_time_95 = time.time()
    forecasts_95 = mod_95.predict(test_df_list[i])
    forec_end_time_95 = time.time()
    forec_time_95 = forec_end_time_95 - forec_start_time_95
    forec_time_95_tot += forec_time_95
    
    # Compute RMSE and MAE for 1 day, 1 week, and 2 week time intervals in the test set
    rmse_1_day = mean_squared_error(test_df_list[i].y[0:96], 
                                    forecasts.yhat[0:96],
                                    squared=False)
    mae_1_day = mean_absolute_error(test_df_list[i].y[0:96], 
                                    forecasts.yhat[0:96])
    rmse_1_week = mean_squared_error(test_df_list[i].y[0:(len(test_df_list[i].y)//2)], 
                                     forecasts.yhat[0:(len(test_df_list[i].y)//2)], 
                                     squared=False)
    mae_1_week = mean_absolute_error(test_df_list[i].y[0:(len(test_df_list[i].y)//2)], 
                                     forecasts.yhat[0:(len(test_df_list[i].y)//2)])
    rmse_2_week = mean_squared_error(test_df_list[i].y, 
                                     forecasts.yhat, 
                                     squared=False)
    mae_2_week = mean_absolute_error(test_df_list[i].y,
                                     forecasts.yhat)
    
    # Save the forecasts to each relevant dictionary
    forecast_dict[i] = forecasts
    forecast_dict_95[i] = forecasts_95
    
    # Append the metrics to each respective list
    rmse_1_day_list.append(rmse_1_day)
    mae_1_day_list.append(mae_1_day)
    rmse_1_week_list.append(rmse_1_week)
    mae_1_week_list.append(mae_1_week)
    rmse_2_week_list.append(rmse_2_week)
    mae_2_week_list.append(mae_2_week)


INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


Initial log joint probability = -149.145
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      92       12416.4   1.00695e-05       516.507   2.017e-08       0.001      163  LS failed, Hessian reset 
      99       12416.4   1.27997e-06       445.149      0.5212      0.5212      172   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     116       12416.4    1.2502e-07       468.222       1.875      0.1875      195   
Optimization terminated normally: 
  Convergence detected: relative gradient magnitude is below tolerance


INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


Initial log joint probability = -149.145
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      92       12416.4   1.00695e-05       516.507   2.017e-08       0.001      163  LS failed, Hessian reset 
      99       12416.4   1.27997e-06       445.149      0.5212      0.5212      172   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     116       12416.4    1.2502e-07       468.222       1.875      0.1875      195   
Optimization terminated normally: 
  Convergence detected: relative gradient magnitude is below tolerance


INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


...

Initial log joint probability = -376.619
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      77       12000.6   0.000469271       5045.43   8.738e-08       0.001      146  LS failed, Hessian reset 
      99       12001.9    1.9932e-06        4653.7           1           1      174   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     149         12002   5.66683e-09       5152.09      0.2227      0.2227      235   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance


INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


Initial log joint probability = -258.426
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12658.7    8.0551e-07       4957.18           1           1      134   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     116       12658.7   4.66649e-09       4629.74      0.2085      0.2085      159   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance


INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


Initial log joint probability = -258.426
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       12658.7    8.0551e-07       4957.18           1           1      134   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     116       12658.7   4.66649e-09       4629.74      0.2085      0.2085      159   
Optimization terminated normally: 
  Convergence detected: absolute parameter change was below tolerance


In [33]:
# Total Model Fitting Time (Including Cross Validation)
round((mod_fit_time_tot + (utah_end_time - utah_start_time) + (portland_end_time - portland_start_time) + (england_end_time - england_start_time)), 2)

7084.12

In [34]:
round((mod_fit_time_95_tot + (utah_end_time - utah_start_time) + (portland_end_time - portland_start_time) + (england_end_time - england_start_time)), 2)

7084.08

In [69]:
round((mod_fit_time_tot + mod_fit_time_95_tot + (utah_end_time - utah_start_time) + (portland_end_time - portland_start_time) + (england_end_time - england_start_time)), 2)

7194.3

In [35]:
# Total Forecasting Time
round(forec_time_tot, 2)

130.52

In [36]:
round(forec_time_95_tot, 2)

129.96

In [70]:
round((forec_time_tot+forec_time_95_tot), 2)

260.48

## Raw Point Forecast Performance Metrics
In this section, we simply print the performance metrics on the test data

In [37]:
np.mean(rmse_1_day_list)

70.72820979103658

In [38]:
np.mean(mae_1_day_list)

52.861713771600705

In [39]:
np.mean(rmse_1_week_list)

72.43187133715546

In [40]:
np.mean(rmse_2_week_list)

76.43189743502815

In [41]:
np.mean(mae_1_week_list)

53.227041417331655

In [42]:
np.mean(mae_2_week_list)

55.93221051291588

## Scaled Point Forecast Performance Metrics
In this section, we examine the scaled performance metrics on the test data

In [43]:
# Create three empty lists, one for each time frame
test_df_1_day_means = list()
test_df_1_week_means = list()
test_df_2_week_means = list()

for i in range(len(test_df_list)):
    # For each time series and time frame, compute the mean and append to the respective list 
    mean_1_day = np.mean(test_df_list[i].y[0:96])
    mean_1_week = np.mean(test_df_list[i].y[0:(len(test_df_list[i].y)//2)])
    mean_2_week = np.mean(test_df_list[i].y)
    
    test_df_1_day_means.append(mean_1_day)
    test_df_1_week_means.append(mean_1_week)
    test_df_2_week_means.append(mean_2_week)

In [44]:
np.mean(np.array(rmse_1_day_list)/np.array(test_df_1_day_means))

0.2918921769530868

In [45]:
np.mean(np.array(mae_1_day_list)/np.array(test_df_1_day_means))

0.2203890032915859

In [46]:
np.mean(np.array(rmse_1_week_list)/np.array(test_df_1_week_means))

0.3020870914926251

In [47]:
np.mean(np.array(mae_1_week_list)/np.array(test_df_1_week_means))

0.22299805056968403

In [48]:
np.mean(np.array(rmse_2_week_list)/np.array(test_df_2_week_means))

0.321485553368326

In [49]:
np.mean(np.array(mae_2_week_list)/np.array(test_df_2_week_means))

0.23686854670391053

## Interval Results

In [50]:
# Examine some sample forecast results which include the PIs
forecast_dict[0].head()

ds       trend  yhat_lower  yhat_upper  trend_lower  \
0 2019-07-10 14:59:00  266.587262  284.987372  507.079721   266.587262   
1 2019-07-10 15:14:00  266.590928  289.759168  508.024422   266.590928   
2 2019-07-10 15:29:00  266.594593  291.949009  506.944337   266.594593   
3 2019-07-10 15:44:00  266.598259  289.544036  508.157278   266.598259   
4 2019-07-10 15:59:00  266.601925  283.372895  513.028280   266.601925   

   trend_upper  additive_terms  additive_terms_lower  additive_terms_upper  \
0   266.587262      127.549217            127.549217            127.549217   
1   266.590928      129.892105            129.892105            129.892105   
2   266.594593      131.285108            131.285108            131.285108   
3   266.598259      131.666725            131.666725            131.666725   
4   266.601925      130.994834            130.994834            130.994834   

        daily  daily_lower  daily_upper    weekly  weekly_lower  weekly_upper  \
0  120.102747   120.102747   120.102747  7.446470      7.446470      7.446470   
1  122.533659   122.533659   122.533659  7.358445      7.358445      7.358445   
2  124.017965   124.017965   124.017965  7.267143      7.267143      7.267143   
3  124.493991   124.493991   124.493991  7.172734      7.172734      7.172734   
4  123.919438   123.919438   123.919438  7.075397      7.075397      7.075397   

   multiplicative_terms  multiplicative_terms_lower  \
0                   0.0                         0.0   
1                   0.0                         0.0   
2                   0.0                         0.0   
3                   0.0                         0.0   
4                   0.0                         0.0   

   multiplicative_terms_upper        yhat  
0                         0.0  394.136479  
1                         0.0  396.483032  
2                         0.0  397.879701  
3                         0.0  398.264984  
4                         0.0  397.596759

In [51]:
# Create a function to compute the interval score
def interval_score(true_values, lower, upper, interval_range):
    """ Function which takes in the true values, the upper and lower bounds of PIs, and the PI level (e.g., 90%)
        and from these inputs, computes the interval score for each prediction
    """
    
    # Compute alpha from the interval range
    alpha = 100*(1-interval_range)
    
    # Save the upper, lower, and true_values as numpy arrays for computation purposes
    upper = np.array(upper)
    lower = np.array(lower)
    true_values = np.array(true_values)
    
    # Compute the lower component of the interval score - just a boolean for true below interval
    def lower_ind(true,low):
        if true<low:
            return 1
        else:
            return 0
        
    # Computer the upper component of the interval score - similar boolean for true above interval
    def upper_ind(true,up):
        if true>up:
            return 1
        else:
            return 0
        
    # Computer the actual score for each obsveration - formula here: https://epiforecasts.io/scoringutils/reference/interval_score.html
    scores = (upper-lower) + (2/alpha)*(lower-true_values)*(lower > true_values) + (2/alpha)*(true_values-upper)*(true_values > upper)
    
    # Return the scores array
    return scores

In [52]:
# Create empty lists to save the interval scores to for each time series and prediction time frame
int_95_scores_1_day = []
int_80_scores_1_day = []

int_95_scores_1_week = []
int_80_scores_1_week = []

int_95_scores = []
int_80_scores = []

# Loop through each test data frame
for i in range(len(test_df_list)):
    
    # Get the true vales
    true_vals_i = test_df_list[i].y
    
    # Grab the intervals from the forecasts
    lo_80_i = forecast_dict[i].yhat_lower
    hi_80_i = forecast_dict[i].yhat_upper
    
    lo_95_i = forecast_dict_95[i].yhat_lower
    hi_95_i = forecast_dict_95[i].yhat_upper
    
    # Compute the interval scores for the 2-week horizon
    int_score_80 = interval_score(true_vals_i,
                                  lo_80_i,
                                  hi_80_i,
                                  0.8)
    int_score_95 = interval_score(true_vals_i,
                                  lo_95_i,
                                  hi_95_i,
                                  0.95)
    
    # Compute for 1-day horizon
    int_score_80_1_day = interval_score(true_vals_i[0:96],
                                        lo_80_i[0:96],
                                        hi_80_i[0:96],
                                        0.8)
    int_score_95_1_day = interval_score(true_vals_i[0:96],
                                        lo_95_i[0:96],
                                        hi_95_i[0:96],
                                        0.95)
    
    # Compute for 1-week horizon
    int_score_80_1_week = interval_score(true_vals_i[0:(len(test_df_list[i].y)//2)],
                                        lo_80_i[0:(len(test_df_list[i].y)//2)],
                                        hi_80_i[0:(len(test_df_list[i].y)//2)],
                                        0.8)
    int_score_95_1_week = interval_score(true_vals_i[0:(len(test_df_list[i].y)//2)],
                                        lo_95_i[0:(len(test_df_list[i].y)//2)],
                                        hi_95_i[0:(len(test_df_list[i].y)//2)],
                                        0.95)
    
    # Append the means of the scores to the respective lists
    int_80_scores_1_day.append(np.mean(int_score_80_1_day))
    int_95_scores_1_day.append(np.mean(int_score_95_1_day))
    
    int_80_scores_1_week.append(np.mean(int_score_80_1_week))
    int_95_scores_1_week.append(np.mean(int_score_95_1_week))
    
    int_80_scores.append(np.mean(int_score_80))
    int_95_scores.append(np.mean(int_score_95))

### One Day

In [53]:
# Examine the mean interval scores for each forecast horizon
np.mean(int_80_scores_1_day)

182.38354771346448

In [54]:
np.mean(int_95_scores_1_day)

278.14644171664605

In [55]:
np.mean(np.array(int_80_scores_1_day)/np.array(test_df_1_day_means))

0.7583934433663566

In [56]:
np.mean(np.array(int_95_scores_1_day)/np.array(test_df_1_day_means))

1.1567271701238742

### One Week

In [57]:
np.mean(int_80_scores_1_week)

183.68467156716065

In [58]:
np.mean(int_95_scores_1_week)

281.02806202525346

In [59]:
np.mean(np.array(int_80_scores_1_week)/np.array(test_df_1_week_means))

0.7635749194332359

In [60]:
np.mean(np.array(int_95_scores_1_week)/np.array(test_df_1_week_means))

1.1724132048776

### Full 

In [61]:
np.mean(int_80_scores)

189.98823932675458

In [62]:
np.mean(int_95_scores)

293.2159771762317

In [63]:
np.mean(np.array(int_80_scores)/np.array(test_df_2_week_means))

0.8211715774159525

In [64]:
np.mean(np.array(int_95_scores)/np.array(test_df_2_week_means))

1.278176177208016

In [65]:
pred_int_df = pd.DataFrame()

for i in range(76):
    
    true_vals_i = test_df_list[i].y.to_list()
    
    # Grab the intervals from the forecasts
    lo_80_i = forecast_dict[i].yhat_lower.to_list()
    hi_80_i = forecast_dict[i].yhat_upper.to_list()
    
    lo_95_i = forecast_dict_95[i].yhat_lower.to_list()
    hi_95_i = forecast_dict_95[i].yhat_upper.to_list()
    
    pred_int_df_i = pd.DataFrame({"ts_index": i, 
                                  "actual": true_vals_i,
                                  "pct_80_lo": lo_80_i,
                                  "pct_80_hi": hi_80_i,
                                  "pct_95_lo": lo_95_i,
                                  "pct_95_hi": hi_95_i
                                 })

    pred_int_df = pred_int_df.append(pred_int_df_i)

In [66]:
pred_int_df['cover_80'] = np.where(pred_int_df['actual']<pred_int_df['pct_80_lo'], 
                                1, 
                                np.where(pred_int_df['actual']>pred_int_df['pct_80_hi'],
                                        1,
                                        0))
pred_int_df['cover_95'] = np.where(pred_int_df['actual']<pred_int_df['pct_95_lo'], 
                                1, 
                                np.where(pred_int_df['actual']>pred_int_df['pct_95_hi'],
                                        1,
                                        0))

In [67]:
# Save the performance metrics into a data frame and then into a csv file
prophet_results = pd.DataFrame(list(zip(rmse_1_week_list, rmse_2_week_list, mae_1_week_list, mae_2_week_list)),
                               columns=["rmse_1_week", "rmse_2_week", "mae_1_week", "mae_2_week"])
prophet_results.to_csv("Results/Univariate/Prophet/prophet_performance.csv", index=False)

In [68]:
# Save the raw forecasts from each model (80% and 95%) into their own DFs and then CSV files

# Initialize empty dfs
forecasts_df = pd.DataFrame()
forecasts_df_95 = pd.DataFrame()

# For each time series
for i in range(len(forecast_dict)):
    # Append 80% interval forecasts to DF
    forecast_df_sub = forecast_dict[i]
    forecast_df_sub["ts_index"] = i
    forecasts_df = forecasts_df.append(forecast_df_sub)
    
    # Append 95% interval forecasts to DF
    forecast_df_sub_95 = forecast_dict_95[i]
    forecast_df_sub_95["ts_index"] = i
    forecasts_df_95 = forecasts_df_95.append(forecast_df_sub_95)
    
# Write to CSV
forecasts_df.to_csv("Results/Univariate/Prophet/raw_prophet_forecasts.csv")
forecasts_df_95.to_csv("Results/Univariate/Prophet/raw_prophet_forecasts_95.csv")